# Model Loading and Preparation

In [ ]:
import tensorflow as tf
import numpy as np
import json
import requests
from PIL import Image
from io import BytesIO
from huggingface_hub import snapshot_download

!mkdir('model')
# Download the entire model directory
model_dir = snapshot_download(repo_id="eligapris/maize-diseases-detection",
    local_dir="model")

# Load the model
model = tf.saved_model.load('model')



# Image Download and Disease Prediction

This section downloads an image of a maize leaf and uses the loaded model to predict any potential diseases or issues.

In [46]:

# Now you can use the model for inference
# Load and preprocess the image
# url = 'https://plantvillage-production-new.s3.amazonaws.com/images/pics/000/062/234/original/5937333353_ea848b13e5_o.jpg'
url = 'https://cropwatch.unl.edu/documents/Corn-southern-rust-F1.jpg'
response = requests.get(url)

img = Image.open(BytesIO(response.content))
img = img.resize((300, 300 * img.size[1] // img.size[0]))
img_array = np.array(img)[None]

# Make prediction
inp = tf.constant(img_array, dtype='float32')
prediction = model(inp)[0].numpy()

# Load class names
with open('model/classes.json', 'r') as f:
    class_names = json.load(f)

# Get the predicted class
predicted_class = list(class_names.keys())[prediction.argmax()]
print(f"Predicted class: {predicted_class}")

Predicted class: Common_Rust


# Comprehensive Maize Disease Prediction and Insights

This section provides detailed predictions for potential maize diseases identified in the input image. It offers further insights and information about the predicted diseases, including their characteristics, causes, and potential management strategies.

In [47]:
# Now you can use the model for inference
# Load and preprocess the image
url = 'https://cropwatch.unl.edu/image/969985-version%3D1.0%26t%3D1249303176000.jpg'
response = requests.get(url)

img = Image.open(BytesIO(response.content))
img = img.resize((300, 300 * img.size[1] // img.size[0]))
img_array = np.array(img)[None]

# Make prediction
inp = tf.constant(img_array, dtype='float32')
prediction = model(inp)[0].numpy()

# Load class names and details
with open('model/classes_detailed.json', 'r') as f:
    data = json.load(f)

class_names = data['classes']
class_details = data['details']

# Get the predicted class
predicted_class = list(class_names.keys())[prediction.argmax()]
predicted_class_label = class_names[predicted_class]

print(f"Predicted class: {predicted_class} (Label: {predicted_class_label})")

# Print detailed information about the predicted class
if predicted_class in class_details:
    details = class_details[predicted_class]
    print("\nDetailed Information:")
    for key, value in details.items():
        if isinstance(value, list):
            print(f"{key.capitalize()}:")
            for item in value:
                print(f"  - {item}")
        else:
            print(f"{key.capitalize()}: {value}")

# Print general notes
print("\nGeneral Notes:")
for note in data['general_notes']:
    print(f"- {note}")

Predicted class: Common_Rust (Label: 3)

Detailed Information:
Causative_agent: Puccinia sorghi
Symptoms:
  - Small, elongate, powdery pustules over both surfaces of the leaves
  - Pustules are dark brown in early stages of infection
  - Later, the epidermis is ruptured and the lesions turn black as the plant matures
Environmental_conditions:
  - Found worldwide in subtropical, temperate, and highland environments with high humidity
Impact: Can reduce yield, especially if infection is severe before or during tasseling
Notes:
  - Most conspicuous when plants approach tasseling
  - Alternate host (Oxalis spp.) may show light orange colored pustules

General Notes:
- Early detection and proper identification of these diseases are crucial for effective management.
- Integrated pest management strategies, including resistant varieties, crop rotation, and timely fungicide applications, can help control these diseases.
- Climate conditions, particularly humidity and temperature, play a signif